# Introduction/Business Problem

Topic - Mumbai Buyers and Tenants Choice Made Simple

Mumbai, the financial capital of India and the second most populous city in the country.When it comes to choosing a location to buy or take a house on rent,it becomes a difficult choice in Mumbai.

The buyers/tenants face difficulty in knowing the neighborhood well without visting the place. With Mumbai being known for its huge length and breadth, the report should be able to give them a snapshot of the areas they are looking out for.

The data analysis should make it simpler for the prospective buyers and tenants,to help them identify their area of choice.The report will help them in analyzing each area as to what services will be available close by.The report should list the skyscrapers in the particular area and hence the users get to know the name of the buildings,location and the prospective service providers in the neighbourhood.

In [1]:
import numpy as np
from IPython.display import display, HTML
from bs4 import BeautifulSoup
from urllib.request import urlopen
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

import types
import pandas as pd
from botocore.client import Config
import ibm_boto3

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
#import folium
# import k-means from clustering stage
from sklearn.cluster import KMeans
!pip install folium
import folium

     |████████████████████████████████| 94 kB 5.2 MB/s  eta 0:00:01


# Data Section
The data is imported from a csv file which lists all the property data which is available for lease/sale in Mumbai.

The data consists of 34348 rows and 23 columns.As the data is huge we will be cleaning the data so that it becomes easir to understand for sample study.
The following columns will be removed:
1)city
2)desc
3)dev_name
4)floor_count
5)floor_num
6)id
7)id_string
8)post_date
9)poster_name
10)title
11)trans
12)type
13)url

The data which has Nan value will be removed.The duplicate records will also be deleted.
We get 19899 rows.

Further the location count is done,the locations which has less than 50 occurences are taken into account.The subset dataframe of locality,longitude,longitude is created.This data will be passed to Fouresquare API.Only 500 such records are sent to Fouresquare API as it only allows 500 calls a day.
The most common venues will be reported for a particular location which will give the user a clear picture about the most common service providers corresponding to each building and area.

In [2]:
# The code was removed by Watson Studio for sharing.

area  bathroom_num  bedroom_num    city  \
0       350.0           2.0            1  Mumbai   
1       652.0           2.0            1  Mumbai   
2       635.0           2.0            1  Mumbai   
3       540.0           2.0            1  Mumbai   
4       625.0           1.0            1  Mumbai   
...       ...           ...          ...     ...   
34343   700.0           2.0            1  Mumbai   
34344   750.0           2.0            1  Mumbai   
34345   700.0           2.0            1  Mumbai   
34346   750.0           2.0            1  Mumbai   
34347  1100.0           2.0            2  Mumbai   

                                                    desc            dev_name  \
0      2 Bath,Unfurnished,East facing The project has...                 NaN   
1      2 Bath,Semi-Furnished,East facing A 1BHK apart...         Veena Group   
2      2 Bath,Semi-Furnished,4 floor,West facing A be...       Agarwal Group   
3      2 Bath,Semi-Furnished,East facing Essential Se...                 NaN   
4      1 Bath,Furnished,2 floor,North facing 24 hours...    Millennium Group   
...                                                  ...                 ...   
34343  2 Bath,Semi-Furnished,5 floor,North facing 1 B...  Evershine Builders   
34344  2 Bath,Semi-Furnished,7 floor,West facing 1 BH...        Poonam Group   
34345  2 Bath,Semi-Furnished,4 floor,North facing 1 B...        Vinay Unique   
34346  2 Bath,Semi-Furnished,4 floor 1 BHK, Multistor...        Vinay Unique   
34347  2 Bath,Unfurnished,7 floor,South -West facing ...                 NaN   

       floor_count  floor_num      furnishing        id  ...  \
0              NaN        NaN     Unfurnished  45349857  ...   
1              NaN        NaN  Semi-Furnished  45960973  ...   
2              7.0        4.0  Semi-Furnished  46688849  ...   
3              NaN        NaN  Semi-Furnished  44696119  ...   
4              7.0        2.0       Furnished  46742851  ...   
...            ...        ...             ...       ...  ...   
34343          7.0        5.0  Semi-Furnished  46601107  ...   
34344         12.0        7.0  Semi-Furnished  46601343  ...   
34345         12.0        4.0  Semi-Furnished  46600981  ...   
34346         12.0        4.0  Semi-Furnished  46600943  ...   
34347         10.0        7.0     Unfurnished  18660587  ...   

               longitude   post_date       poster_name    price  \
0      72.82588195800781  2020-01-11     Saurabh Patil     9000   
1            72.83359245  2020-01-11    Gorakh  Chavan     8060   
2            72.80161155  2019-12-13      Lokesh Joshi     8000   
3      72.83600616455078  2020-01-13    Sajith  Thomas     8000   
4      72.85016654221559  2019-12-17  Charmaine  Gomez     9000   
...                  ...         ...               ...      ...   
34343        72.80061282  2019-12-09    Rambahad Singh     7000   
34344                0.0  2019-12-09    Rambahad Singh     6500   
34345         72.7955643  2019-12-09    Rambahad Singh     6500   
34346         72.7955643  2019-12-09    Rambahad Singh     6500   
34347                0.0  2019-12-30     Rishi  Dusija  1200000   

                    project  \
0                       NaN   
1             Veena Dynasty   
2         Agarwal Lifestyle   
3                       NaN   
4            Mittal Enclave   
...                     ...   
34343       Evershine Homes   
34344        Poonam Heights   
34345  Vinay Unique Heights   
34346  Vinay Unique Heights   
34347                   NaN   

                                                   title  trans  \
0                 1 BHK Apartment for Rent in Malad West   Rent   
1       1 BHK Apartment for Rent in Veena Dynasty, Vasai   Rent   
2      1 BHK Apartment for Rent in Agarwal Lifestyle,...   Rent   
3                 1 BHK Apartment for Rent in Vasai East   Rent   
4      1 BHK Apartment for Rent in Mittal Enclave, Na...   Rent   
...                                                  ...    ...   
34343  

In [3]:
df_data1 = df_data.drop(['city','desc','dev_name','floor_count', 'floor_num', 'id', 'id_string','post_date', 'poster_name',
       'title', 'trans', 'type', 'url'],axis='columns')


#df_data1 = df_data1.drop(df_data[df_data.latitude=='0.0'])
df_data1.shape
df_data1 =df_data1[df_data1['latitude'] !=0.0]
df_data1 =df_data1[df_data1['longitude'] !=0.0]
df_data1 =df_data1[df_data1['locality'] !='']
df_data1.loc[(df_data1!=0.0).any(axis=1)]
indexNames = df_data1[(df_data1['latitude'] =='0.0') & (df_data1['longitude'] == '0.0')].index
df_data1.drop(indexNames , inplace=True)
df_data1.drop_duplicates()
df_data1.reset_index(drop=True, inplace=True)
df_data1['user_type'].unique()
df_data1.isnull().sum()
df_ready = df_data1.dropna()
df_ready.isnull().sum()
df_ready

area  bathroom_num  bedroom_num      furnishing          latitude  \
1      652.0           2.0            1  Semi-Furnished       19.41070368   
2      635.0           2.0            1  Semi-Furnished       19.46703238   
4      625.0           1.0            1       Furnished  19.3602150985917   
5      630.0           2.0            1     Unfurnished         19.470536   
6      690.0           2.0            1       Furnished       19.46825836   
...      ...           ...          ...             ...               ...   
24795  700.0           2.0            1  Semi-Furnished       19.46778327   
24796  680.0           2.0            1     Unfurnished         19.471987   
24797  700.0           2.0            1  Semi-Furnished       19.46825836   
24798  700.0           2.0            1  Semi-Furnished         19.470357   
24799  750.0           2.0            1  Semi-Furnished         19.470357   

           locality          longitude  price               project user_type  
1             Vasai        72.83359245   8060         Veena Dynasty     Agent  
2             Virar        72.80161155   8000     Agarwal Lifestyle     Agent  
4      Naigaon East  72.85016654221559   9000        Mittal Enclave     Owner  
5        Virar West          72.808309   8000      Poonam Park View     Agent  
6             Virar        72.80061282   8500       Evershine Homes     Agent  
...             ...                ...    ...                   ...       ...  
24795         Virar        72.79647106   6500        Cosmos Regency     Agent  
24796    Virar West          72.800387   6500       Ekta Parksville     Agent  
24797         Virar        72.80061282   7000       Evershine Homes     Agent  
24798         Virar         72.7955643   6500  Vinay Unique Heights     Agent  
24799         Virar         72.7955643   6500  Vinay Unique Heights     Agent  

[17301 rows x 10 columns]

Drop locations that have less than 10 occurences

In [4]:
location = df_ready['locality'].value_counts()
#print(location)
print(location.values.sum())
len(location[location<=50])
location_stats_less_than_1000 = location[location<=50]
#print(location_stats_less_than_500)
df = location_stats_less_than_1000.sort_index().rename_axis('l').reset_index(name='count')
print(df['l'].value_counts())
#print(df.shape)
#print(df['l'])
#print(df_ready.locality.isin(df['l']))
df_ready = df_ready[df_ready['locality'].isin(df['l'])]
#df_ready.drop_duplicates(['locality','latitude','longitude'])
df_ready.reset_index(drop=True, inplace=True)
location = df_ready['locality'].value_counts()
df_location=df_ready.loc[:, ['locality','latitude','longitude']]
#arr = np.array(df_location)
#df_loc = pd.DataFrame(data=arr.flatten())
#print(df_loc)
print(df_location)
df_location.drop_duplicates()
df_location.reset_index(drop=True, inplace=True)
df_location = df_location.head(500)
#df_final = df_ready[df_ready['locality'].isin(df_location['locality'])]
print(df_location)
#df_ready.drop(df_[ready[df_ready.locality.isin(df['l']])].index.tolist())
#df_final

17301
Jankalyan Nagar            1
Amar Nagar                 1
Worli Sea Face             1
Basant Garden              1
Garodia Nagar              1
                          ..
Saki Vihar Road            1
Govandi                    1
Azad Nagar Versova Road    1
Crompton Greaves           1
Dongarpada                 1
Name: l, Length: 415, dtype: int64
             locality            latitude          longitude
0               Vasai         19.41070368        72.83359245
1          Vasai West         19.37068218        72.81293356
2          Vasai East           19.406578          72.838665
3              Kalyan  19.261873899999998         73.1197768
4              Kalyan  19.261873899999998         73.1197768
...               ...                 ...                ...
2910  Nalasopara West  19.429026666666672  72.81065666666667
2911  Nalasopara East  19.410505999999998          72.832122
2912         Nai Gaon         19.35996123        72.85769846
2913  Nalasopara East  19.4105

In [77]:
CLIENT_ID = 'WPHQ4ZFRPXYO2TFLNZRM2BQ1WLTXT40FAQKZ4BYO1USMQNUI' # your Foursquare ID
CLIENT_SECRET = 'CFJYBM04XN02NANX14R5XZKNKFUJLPXIG2S23BG4ZKLISRWG' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: WPHQ4ZFRPXYO2TFLNZRM2BQ1WLTXT40FAQKZ4BYO1USMQNUI
CLIENT_SECRET:CFJYBM04XN02NANX14R5XZKNKFUJLPXIG2S23BG4ZKLISRWG


In [78]:
def getNearbyVenues(names, latitudes, longitudes, radius=5000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
        print(url)  
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [79]:
mumbai_venues = getNearbyVenues(names=df_location['locality'],
                                   latitudes=df_location['latitude'],
                                   longitudes=df_location['longitude']
                                  )
mumbai_venues.groupby('Neighborhood').count()

Vasai
https://api.foursquare.com/v2/venues/explore?&client_id=WPHQ4ZFRPXYO2TFLNZRM2BQ1WLTXT40FAQKZ4BYO1USMQNUI&client_secret=CFJYBM04XN02NANX14R5XZKNKFUJLPXIG2S23BG4ZKLISRWG&v=20180605&ll=19.41070368,72.83359245&radius=5000&limit=100
Vasai West
https://api.foursquare.com/v2/venues/explore?&client_id=WPHQ4ZFRPXYO2TFLNZRM2BQ1WLTXT40FAQKZ4BYO1USMQNUI&client_secret=CFJYBM04XN02NANX14R5XZKNKFUJLPXIG2S23BG4ZKLISRWG&v=20180605&ll=19.37068218,72.81293356&radius=5000&limit=100
Vasai East
https://api.foursquare.com/v2/venues/explore?&client_id=WPHQ4ZFRPXYO2TFLNZRM2BQ1WLTXT40FAQKZ4BYO1USMQNUI&client_secret=CFJYBM04XN02NANX14R5XZKNKFUJLPXIG2S23BG4ZKLISRWG&v=20180605&ll=19.406578,72.838665&radius=5000&limit=100
Kalyan
https://api.foursquare.com/v2/venues/explore?&client_id=WPHQ4ZFRPXYO2TFLNZRM2BQ1WLTXT40FAQKZ4BYO1USMQNUI&client_secret=CFJYBM04XN02NANX14R5XZKNKFUJLPXIG2S23BG4ZKLISRWG&v=20180605&ll=19.261873899999998,73.1197768&radius=5000&limit=100
Kalyan
https://api.foursquare.com/v2/venues/explore

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                                    
Akurli Nagar                                      200                     200   
Andheri                                           100                     100   
Asha Nagar                                        700                     700   
Ashok Nagar Western Mumbai                        200                     200   
Atur Park Colony Bungalow                         100                     100   
...                                               ...                     ...   
Worli Naka Acharaya Atre Chowk                    100                     100   
Worli Sea Face                                    100                     100   
Yeshodham                                         100                     100   
Yogi Jayraj Nagar                                 100                     100   
Yogi Nagar                                        100                     100   

                                Venue  Venue Latitude  Venue Longitude  \
Neighborhood                                                             
Akurli Nagar                      200             200              200   
Andheri                           100             100              100   
Asha Nagar                        700             700              700   
Ashok Nagar Western Mumbai        200             200              200   
Atur Park Colony Bungalow         100             100              100   
...                               ...             ...              ...   
Worli Naka Acharaya Atre Chowk    100             100              100   
Worli Sea Face                    100             100              100   
Yeshodham                         100             100              100   
Yogi Jayraj Nagar                 100             100              100   
Yogi Nagar                        100             100              100   

                                Venue Category  
Neighborhood                                    
Akurli Nagar                               200  
Andheri                                    100  
Asha Nagar                                 700  
Ashok Nagar Western Mumbai                 200  
Atur Park Colony Bungalow                  100  
...                                        ...  
Worli Naka Acharaya Atre Chowk             100  
Worli Sea Face                             100  
Yeshodham                                  100  
Yogi Jayraj Nagar                          100  
Yogi Nagar                                 100  

[150 rows x 6 columns]

In [100]:
# one hot encoding
mumbai_onehot = pd.get_dummies(mumbai_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
mumbai_onehot['Neighborhood'] = mumbai_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [mumbai_onehot.columns[-1]] + list(mumbai_onehot.columns[:-1])
mumbai_onehot = mumbai_onehot[fixed_columns]

mumbai_onehot.head(10)
mumbai_onehot.shape
mumbai_grouped = mumbai_onehot.groupby('Neighborhood').mean().reset_index()
mumbai_grouped.shape

(150, 179)

In [101]:
num_top_venues = 10

for hood in mumbai_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = mumbai_grouped[mumbai_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Akurli Nagar----
                  venue  freq
0     Indian Restaurant  0.10
1  Fast Food Restaurant  0.06
2           Coffee Shop  0.06
3         Shopping Mall  0.04
4            Donut Shop  0.04
5            Restaurant  0.04
6        Ice Cream Shop  0.04
7                   Gym  0.03
8           Pizza Place  0.03
9        Clothing Store  0.03


----Andheri----
                venue  freq
0   Indian Restaurant  0.11
1               Hotel  0.09
2  Italian Restaurant  0.06
3      Ice Cream Shop  0.06
4              Lounge  0.05
5           Multiplex  0.04
6         Coffee Shop  0.04
7              Bakery  0.03
8             Brewery  0.03
9  Chinese Restaurant  0.02


----Asha Nagar----
                  venue  freq
0     Indian Restaurant  0.08
1           Coffee Shop  0.06
2        Ice Cream Shop  0.05
3  Fast Food Restaurant  0.05
4            Restaurant  0.04
5                   Gym  0.03
6            Donut Shop  0.03
7         Shopping Mall  0.03
8    Chinese Restaurant  0.03
9 

In [119]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [120]:
from IPython.display import display, HTML
def display_print(df2):
    return display( HTML( df2.to_html().replace("\\n","<br>") ) )

In [127]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = mumbai_grouped['Neighborhood']

for ind in np.arange(mumbai_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(mumbai_grouped.iloc[ind, :], num_top_venues)

print(display_print(neighborhoods_venues_sorted))

None


In [128]:
# set number of clusters
kclusters = 5

mumbai_grouped_clustering = mumbai_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(mumbai_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 3, 2, 2, 3, 4, 0, 4, 0, 4], dtype=int32)

In [129]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
df_final = df_ready[df_ready['locality'].isin(df_location['locality'])]
mumbai_merged = df_final#df_ready

# merge manhattan_grouped with toronto_data to add latitude/longitude for each neighborhood
mumbai_merged = mumbai_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='locality')
#mumbai_merged = mumbai_merged.drop(mumbai_merged.columns[[5,6]], axis=1)
#mumbai_merged.reset_index(drop=True, inplace=True)
print(display_print(mumbai_merged))
mumbai_merged.shape

None


(1811, 21)

In [130]:
from geopy.geocoders import Nominatim
address = 'Mumbai,IN'

geolocator = Nominatim(user_agent="mumbai_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Mumbai City are {}, {}.'.format(latitude, longitude))
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]
# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(mumbai_merged['latitude'], mumbai_merged['longitude'], mumbai_merged['locality'], mumbai_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[np.isnan(cluster)-1],
        fill=True,
        fill_color=rainbow[np.isnan(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

The geograpical coordinate of Mumbai City are 19.0759899, 72.8773928.
